In [361]:
import os
import re
import string
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tqdm
import pycountry_convert as pc


# Plotly
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

from geopy.geocoders import Nominatim
from geopy.point import Point

pd.set_option('display.max_columns', None)

### Get list of file names in the directory

In [8]:
filename = os.listdir('data')
# get length of the list
filename

['watchedVideo.csv',
 '.DS_Store',
 'feeds.csv',
 'users.csv',
 'videos.csv',
 'tables.txt']

## User data
#### Load the data

In [346]:
users = pd.read_csv('data/users.csv')
users.head()

Unnamed: 0                                    id           created_at  \
0           0  37e369a8-4477-4d5d-acd7-4e3b8059586e  2021-03-23 00:24:53   
1           1  27cf0bb6-3488-4662-916d-3ad04eeec9ca  2021-04-09 19:55:07   
2           2  5ebd5e12-ba2a-4bf9-b7e4-92ad24711cd4  2021-04-08 21:48:45   
3           3  30986592-0cbf-43bb-83ed-7501ab3bd373  2021-05-15 00:45:51   
4           4  25b49125-34d1-4694-a4a9-8415bcc3567b  2021-07-05 04:08:53   

         class                coordinates  
0      Creator    ('36.76775', '2.95924')  
1       Viewer   ('43.71032', '-1.05366')  
2  Super Gamer       ('51.26', '-2.1875')  
3      Creator  ('40.65538', '-74.38987')  
4       Viewer  ('35.61452', '-88.81395')

In [10]:
users.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   Unnamed: 0   1000 non-null   int64 
 1   id           1000 non-null   object
 2   created_at   1000 non-null   object
 3   class        1000 non-null   object
 4   coordinates  1000 non-null   object
dtypes: int64(1), object(4)
memory usage: 39.2+ KB


#### Check for uniqueness

In [437]:
users.nunique()

id              1000
created_at      1000
class              5
coordinates      626
lat              626
long             625
country_code     109
continent          6
dtype: int64

#### Drop unnessary column

In [347]:
users = users.drop('Unnamed: 0', axis=1)

In [452]:
x = users['class'].unique()
y = users['class'].value_counts()
fig = px.bar(x=x, y=y, text=y)
fig.update_xaxes(title='Classes')
fig.update_yaxes(title='Number of Users')
fig.show()

In [12]:
users.groupby('class').count()

Unnamed: 0   id  created_at  coordinates
class                                                  
Creator               186  186         186          186
Gamer                 213  213         213          213
Super Creator         206  206         206          206
Super Gamer           209  209         209          209
Viewer                186  186         186          186

#### Get the coordinates

In [348]:
users['lat'] = users.coordinates.apply(lambda x: float(x.split(',')[0][2:-1]))

In [349]:
users['long'] = users.coordinates.apply(lambda x: float(x.split(',')[1][2:-2]))

In [476]:
# Get a bounding box of the coordinates.
BBox = (users.long.min(), users.long.max(), users.lat.min(), users.lat.max())
BBox

(-122.86705, 178.00417, -54.8, 68.79833)

#### Plot user geographical location

In [352]:
fig = go.Figure()
fig = px.scatter(users, x='long', y='lat', color='class')
# fig.add_trace(go.Scatter(x=users['lat'], y=users['long'], mode='markers'))
fig.add_layout_image(
    dict(
        source='https://upload.wikimedia.org/wikipedia/commons/thumb/f/fc/No_colonies_blank_world_map.png/1200px-No_colonies_blank_world_map.png',
        xref="x",
        yref="y",
        x=-140,
        y=85,
        sizex=345,
        sizey=144,
        opacity=0.5,
        sizing='stretch',
        layer='below'))

fig.update_traces(marker=dict(size=10),
                  selector=dict(mode='markers'))
fig.update_xaxes(showgrid=False)
fig.update_yaxes(showgrid=False)

fig.update_layout(template="plotly_white")
fig.show()

In [367]:
tqdm.tqdm.pandas()

In [394]:
def get_country_code(lat, long):
    geolocator = Nominatim(user_agent="geoapiExercises")
    location = geolocator.reverse(Point(lat, long))
    if location:
        address = location.raw['address']
        country_code = address.get('country_code', '')
        return country_code.upper()
    return    

In [395]:
users['country_code'] = users.progress_apply(lambda users: get_country_code(users['lat'], users['long']), axis=1)

100%|██████████| 1000/1000 [08:22<00:00,  1.99it/s]


In [379]:
def get_continent(country_code):
    if country_code == 'tl':
        return 'AS'
    continent_name = pc.country_alpha2_to_continent_code(country_code.upper())
    return continent_name

In [380]:
users['continent'] = users['country_code'].progress_apply(lambda x: get_continent(x))

100%|██████████| 1000/1000 [00:00<00:00, 80184.75it/s]


In [409]:
fig = px.scatter_geo(users, lat='lat', lon='long', color="class",
                     projection="natural earth")
fig.update_traces(marker=dict(size=5),
                  selector=dict(mode='markers'))

fig.show()

In [419]:
temp = users['continent'].value_counts().reset_index(name='count')
temp['perc'] = temp['count']/temp['count'].sum()

In [438]:
fig = px.bar(temp, x='index', y='count', text=temp['perc'].apply(lambda x: '{0:1.0f}%'.format(x*100)))
fig.update_xaxes(title='Continent')
fig.show()

In [439]:
px.pie(temp, names='index', values='count', title='User By Continent')

In [473]:
temp = users['country_code'].value_counts().reset_index(name='count')
temp['perc'] = temp['count']/temp['count'].sum()

In [474]:
fig = px.bar(temp, x='index', y='count', text=temp['perc'].apply(lambda x: '{0:1.0f}%'.format(x*100)))
fig.update_xaxes(title='Country')
fig.show()

In [485]:
users['date'] = pd.to_datetime(users['created_at'])

In [486]:
max(users['date'])

Timestamp('2021-12-15 06:52:35')

In [487]:
min(users['date'])

Timestamp('2021-01-01 02:31:57')

## Complementary Datasets
### Feeds Data

In [205]:
feeds = pd.read_csv('data/feeds.csv')
feeds

Unnamed: 0                                    id     name
0           0  27a87df4-da75-451f-b8f6-af9dd0a4ee00    music
1           1  42568c8a-efbe-4293-81a3-513e33094ade  fashion
2           2  6894af29-56cc-4b4a-8ee6-be9b3cb3e7f1   sports
3           3  c9d59470-c4ee-43ff-831d-b52508c8d848    games
4           4  582520b2-b30a-4ecb-b1b4-1806672fcfc4   travel
5           5  a8a04865-55d4-4de4-8141-b273b678299f      fun
6           6  644a3cb6-e266-4757-9e96-a3ee049216fe    jokes
7           7  da6c201f-8e50-433c-b2ad-614e42fac047     love
8           8  8078efe7-5bae-4528-9a66-b85904cc73ac    dance
9           9  30134b9e-1b79-43fb-b0c5-373af9237b2c  beaches

In [212]:
feeds = feeds.drop('Unnamed: 0', axis=1)

### Videos Data

In [208]:
videos = pd.read_csv('data/videos.csv')
videos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5000 entries, 0 to 4999
Data columns (total 11 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Unnamed: 0    5000 non-null   int64  
 1   id            5000 non-null   object 
 2   attribute_id  5000 non-null   object 
 3   music_id      5000 non-null   object 
 4   animation_id  5000 non-null   object 
 5   duration      5000 non-null   float64
 6   creator       5000 non-null   object 
 7   created_at    5000 non-null   object 
 8   num_shares    5000 non-null   int64  
 9   game_id       5000 non-null   object 
 10  is_ar         5000 non-null   bool   
dtypes: bool(1), float64(1), int64(2), object(7)
memory usage: 395.6+ KB


In [214]:
videos = videos.drop('Unnamed: 0', axis=1)

In [253]:
videos.columns

Index(['id', 'attribute_id', 'music_id', 'animation_id', 'duration', 'creator',
       'created_at', 'num_shares', 'game_id', 'is_ar'],
      dtype='object')

In [299]:
pd.merge(videos, users[['id', 'class']], left_on='creator', right_on='id').groupby('class').count()

id_x  attribute_id  music_id  animation_id  duration  creator  \
class                                                                          
Creator         963           963       963           963       963      963   
Gamer          1078          1078      1078          1078      1078     1078   
Super Creator  1015          1015      1015          1015      1015     1015   
Super Gamer    1020          1020      1020          1020      1020     1020   
Viewer          924           924       924           924       924      924   

               created_at  num_shares  game_id  is_ar  id_y  
class                                                        
Creator               963         963      963    963   963  
Gamer                1078        1078     1078   1078  1078  
Super Creator        1015        1015     1015   1015  1015  
Super Gamer          1020        1020     1020   1020  1020  
Viewer                924         924      924    924   924

In [276]:
videos.agg(['count', 'nunique'])

id  attribute_id  music_id  animation_id  duration  creator  \
count    5000          5000      5000          5000      5000     5000   
nunique  5000            11        10            15       491      992   

         created_at  num_shares  game_id  is_ar  
count          5000        5000     5000   5000  
nunique        5000          21        5      2

In [285]:
px.histogram(videos, x='duration', color='game_id')

### Watched Video Data

In [241]:
watchedVideo = pd.read_csv('data/watchedVideo.csv')
watchedVideo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   Unnamed: 0   50000 non-null  int64  
 1   coordinates  50000 non-null  object 
 2   os           50000 non-null  object 
 3   duration     50000 non-null  float64
 4   videoId      50000 non-null  object 
 5   userId       50000 non-null  object 
 6   appVersion   50000 non-null  object 
 7   dateTime     50000 non-null  object 
 8   feedId       50000 non-null  object 
dtypes: float64(1), int64(1), object(7)
memory usage: 3.4+ MB


In [278]:
watchedVideo.agg(['count','nunique'])

coordinates     os  duration  videoId  userId  appVersion  dateTime  \
count          50000  50000     50000    50000   50000       50000     50000   
nunique        50000      2       691     5000    1000          10     49649   

         feedId  
count     50000  
nunique      10

In [242]:
watchedVideo = watchedVideo.drop('Unnamed: 0', axis=1)

In [263]:
df = pd.merge(watchedVideo, feeds[['id','name']], left_on='feedId', right_on='id', how='left')\
    .drop(columns=['feedId','id'])\
    .rename(columns={'name':'feed'})

In [264]:
right = videos[['id', 'attribute_id', 'music_id', 'animation_id', 'creator',
       'created_at', 'num_shares', 'game_id', 'is_ar']]

In [266]:
df = pd.merge(df, right, left_on='videoId', right_on='id', how='left')\
    .drop(columns=['id'])

In [458]:
df.head()

coordinates       os  duration  \
0  (Decimal('14.439490'), Decimal('105.291233'))      iOS      3.95   
1  (Decimal('40.866935'), Decimal('-73.845013'))      iOS      5.95   
2    (Decimal('48.666850'), Decimal('9.359456'))      iOS      0.69   
3   (Decimal('5.172365'), Decimal('-74.439009'))  Android      2.81   
4     (Decimal('4.063707'), Decimal('9.606159'))      iOS      5.88   

                                videoId                                userId  \
0  722e110c-2f81-46aa-9c25-4d26fd77519f  317a2bc3-5f95-4d35-9a94-1f2f38424c4f   
1  cc10d153-37f9-42b5-8d78-2365908acf2b  db031c3d-69e4-4c06-91fe-e9be0a3c173c   
2  7f3f7fce-f2ec-4dfd-bac8-92dc7865a365  8fb18b66-f548-42a7-b394-c1be963cac29   
3  8ffc47e3-32ce-4d24-a990-9baac556603b  960fb90e-eddc-478a-a64a-04b9dded3a05   
4  47e70477-7511-4bd0-801b-1651f951002f  1ce0c003-25e7-473f-8796-0fe04d6c275c   

  appVersion             dateTime     feed  \
0      2.2.2  2021-08-04 09:39:07  beaches   
1      2.2.1  2021-07-06 16:32:10    dance   
2      2.2.0  2021-12-06 01:42:02   sports   
3      2.1.2  2021-12-04 21:02:50  fashion   
4      2.1.2  2021-11-28 16:12:39   travel   

                           attribute_id                              music_id  \
0  30fa7949-1cb6-44b1-9c7b-42c7421fc504  19e4db13-d854-4913-a8ca-3612ee1a6071   
1  30fa7949-1cb6-44b1-9c7b-42c7421fc504  4ee0de5b-e27f-4d73-a3c6-52cf26e36c54   
2  c3328117-4129-4d8b-8250-9479e9c6a389  3de11516-8627-47c3-98ab-265b429cac91   
3  25e7fab9-abfb-4a74-a8cb-c3adbc6e3531  3de11516-8627-47c3-98ab-265b429cac91   
4  4712e9e6-bef1-4646-b21e-ca5336901bf9  4ee0de5b-e27f-4d73-a3c6-52cf26e36c54   

                           animation_id                               creator  \
0  ab5dc9f1-deb4-44d4-88ff-62e473a060f4  43e50511-d2be-4b64-b75f-3d1e7bc33fe9   
1  ab5dc9f1-deb4-44d4-88ff-62e473a060f4  335a3eed-f53c-4daa-87b1-1216e6132cc8   
2  08dda558-a151-45a2-8e43-1ba6f2891800  7872da48-f390-4ac6-a53c-324a179e7459   
3  716c02df-bd3a-41c9-b2be-86fb74ff3255  280a7318-4389-4224-952b-74bec71d2e74   
4  2029f213-1719-4108-8125-25d465cf475d  293bcb6f-c892-43aa-a92a-4729ec3513fb   

            created_at  num_shares                               game_id  \
0  2021-07-23 22:53:22          16  8bd4c7be-fe87-45ad-990d-d131cd3d9c77   
1  2021-06-18 00:08:54           5  2609b6b5-3a08-451e-bce5-75fe506559d2   
2  2021-11-28 01:59:34           7  2609b6b5-3a08-451e-bce5-75fe506559d2   
3  2021-09-30 17:17:03          20  6ca0f645-a16b-42b0-9dc2-2ae952c83591   
4  2021-08-11 05:22:30          11  2609b6b5-3a08-451e-bce5-75fe506559d2   

   is_ar        lat  
0  False  14.439490  
1   True  40.866935  
2   True  48.666850  
3   True   5.172365  
4  False   4.063707

In [460]:
df['lat'] = df.coordinates.apply(lambda x: float(x.split(',')[0][10:-2]))
df['long'] = df.coordinates.apply(lambda x: float(x.split(',')[1][10:-3]))

In [466]:
df.head()

coordinates       os  duration  \
0  (Decimal('14.439490'), Decimal('105.291233'))      iOS      3.95   
1  (Decimal('40.866935'), Decimal('-73.845013'))      iOS      5.95   
2    (Decimal('48.666850'), Decimal('9.359456'))      iOS      0.69   
3   (Decimal('5.172365'), Decimal('-74.439009'))  Android      2.81   
4     (Decimal('4.063707'), Decimal('9.606159'))      iOS      5.88   

                                videoId                                userId  \
0  722e110c-2f81-46aa-9c25-4d26fd77519f  317a2bc3-5f95-4d35-9a94-1f2f38424c4f   
1  cc10d153-37f9-42b5-8d78-2365908acf2b  db031c3d-69e4-4c06-91fe-e9be0a3c173c   
2  7f3f7fce-f2ec-4dfd-bac8-92dc7865a365  8fb18b66-f548-42a7-b394-c1be963cac29   
3  8ffc47e3-32ce-4d24-a990-9baac556603b  960fb90e-eddc-478a-a64a-04b9dded3a05   
4  47e70477-7511-4bd0-801b-1651f951002f  1ce0c003-25e7-473f-8796-0fe04d6c275c   

  appVersion             dateTime     feed  \
0      2.2.2  2021-08-04 09:39:07  beaches   
1      2.2.1  2021-07-06 16:32:10    dance   
2      2.2.0  2021-12-06 01:42:02   sports   
3      2.1.2  2021-12-04 21:02:50  fashion   
4      2.1.2  2021-11-28 16:12:39   travel   

                           attribute_id                              music_id  \
0  30fa7949-1cb6-44b1-9c7b-42c7421fc504  19e4db13-d854-4913-a8ca-3612ee1a6071   
1  30fa7949-1cb6-44b1-9c7b-42c7421fc504  4ee0de5b-e27f-4d73-a3c6-52cf26e36c54   
2  c3328117-4129-4d8b-8250-9479e9c6a389  3de11516-8627-47c3-98ab-265b429cac91   
3  25e7fab9-abfb-4a74-a8cb-c3adbc6e3531  3de11516-8627-47c3-98ab-265b429cac91   
4  4712e9e6-bef1-4646-b21e-ca5336901bf9  4ee0de5b-e27f-4d73-a3c6-52cf26e36c54   

                           animation_id                               creator  \
0  ab5dc9f1-deb4-44d4-88ff-62e473a060f4  43e50511-d2be-4b64-b75f-3d1e7bc33fe9   
1  ab5dc9f1-deb4-44d4-88ff-62e473a060f4  335a3eed-f53c-4daa-87b1-1216e6132cc8   
2  08dda558-a151-45a2-8e43-1ba6f2891800  7872da48-f390-4ac6-a53c-324a179e7459   
3  716c02df-bd3a-41c9-b2be-86fb74ff3255  280a7318-4389-4224-952b-74bec71d2e74   
4  2029f213-1719-4108-8125-25d465cf475d  293bcb6f-c892-43aa-a92a-4729ec3513fb   

            created_at  num_shares                               game_id  \
0  2021-07-23 22:53:22          16  8bd4c7be-fe87-45ad-990d-d131cd3d9c77   
1  2021-06-18 00:08:54           5  2609b6b5-3a08-451e-bce5-75fe506559d2   
2  2021-11-28 01:59:34           7  2609b6b5-3a08-451e-bce5-75fe506559d2   
3  2021-09-30 17:17:03          20  6ca0f645-a16b-42b0-9dc2-2ae952c83591   
4  2021-08-11 05:22:30          11  2609b6b5-3a08-451e-bce5-75fe506559d2   

   is_ar        lat        long  
0  False  14.439490  105.291233  
1   True  40.866935  -73.845013  
2   True  48.666850    9.359456  
3   True   5.172365  -74.439009  
4  False   4.063707    9.606159

In [478]:
fig = px.scatter_geo(df, lat='lat', lon='long',color="feed",
                     projection="natural earth")
fig.update_traces(marker=dict(size=1, opacity=0.2),
                  selector=dict(mode='markers'))

fig.show()

In [481]:
temp = df.groupby('os')['userId'].count()

In [482]:
temp

os
Android    25037
iOS        24963
Name: userId, dtype: int64

In [484]:
temp = df.groupby('feed')['userId'].count()
temp

feed
beaches    4895
dance      5012
fashion    5116
fun        4974
games      4989
jokes      4976
love       4939
music      4978
sports     5017
travel     5104
Name: userId, dtype: int64

In [283]:
px.bar(df, x='num_shares', color='os')